# La millionième décimale de $\pi$ (II)

Marc Lorenzi

16 février 2019

In [ ]:
from sympy import *
init_printing()
x = Symbol('x')
import math

Nous allons dans ce notebook nous intéresser à la question suivante : 

Est-il possible de calculer la millionième décimale de $\pi$ 

- __SANS calculer les décimales précédentes__, et
- __En effectuant uniquement des calculs en précision standard__ ?

En 1997, David Bailey, Peter Borwein et Simon Plouffe ont démontré que ceci était possible, _en base 16_. L'aricle original se trouve facilement sur Internet, et il est tout à fait lisible. Pour les lecteurs motivés, en voici la référence :

D. Bailey, P. Borwein, S. Plouffe, _On the Rapid Computation of Various Polylogarithmic Constants_, Mathematics of Computation, Vol 66, Number 218, April 1997, Pages 903-913.


On peut donc déterminer le $d$ième chiffre de $\pi$ en base 16, ainsi que quelques chiffres suivants, en un temps quasi-linéaire et en calculant en précision standard. Nous allons tout d'abord établir la formule qui permet ce calcul, puis faire le dit calcul ...

## 1. Une intégrale

### 1.1 Intégrons une fraction rationnelle

Considérons la fraction rationnelle suivante.

In [ ]:
F = (-8 * x ** 5 - 4 * sqrt(2) * x ** 4 - 8 * x ** 3 + 4 * sqrt(2)) / (1 - x ** 8)
F

Le dénominateur de $F$ est immédiat à factoriser.

In [ ]:
factor(1 - x ** 8)

La décomposition de $F$ en éléments simples est

In [ ]:
apart(F, x)

On en déduit facilement une primitive de $F$.

In [ ]:
G = integrate(F, x)
G

Calculons $\int_0^{\sqrt(2)/2} F(x)dx$.

In [ ]:
G.subs(x, sqrt(2) / 2) - G.subs(x, 0)

In [ ]:
init_printing(pretty_print=False)

### 1.2 Échange d'une intégrale et d'une somme

Faisons maintenant un petit calcul ... On a pour tout $x\in[0,\frac{\sqrt 2} 2]$

$$\frac{-8x^5-4\sqrt 2 x^4-8x^3+4\sqrt 2}{1-x^8}=(-8x^5-4\sqrt 2 x^4-8x^3+4\sqrt 2)\sum_{i=0}^\infty x^{8i}$$

La série convergeant uniformément sur $[0,\frac{\sqrt 2}2]$, on peut échanger la série et l'intégrale :

$$\int_0^{\sqrt 2 / 2}F(x)dx=\sum_{i=0}^\infty\left( -8\int_0^{\sqrt 2 / 2}x^{8i+5}dx-4\sqrt 2 \int_0^{\sqrt 2 / 2}x^{8i+4}dx-8\int_0^{\sqrt 2 / 2}x^{8i+3}dx+4\sqrt 2\int_0^{\sqrt 2 / 2}x^{8i}dx\right)$$

Laissons le reste au lecteur. Le membre de gauche vaut $\pi$ et les intégrales du membre de droite sont faciles à calculer. On obtient

$$\sum_{i=0}^\infty \frac 1 {16^i}\left(\frac{4}{8i+1}-\frac{2}{8i+4}-\frac{1}{8i+5}-\frac{1}{8i+6}\right)=\pi$$

C'est cette dernière formule qui va nous permettre de calculer des décimales de $\pi$. Remarquez les puissances de 16. Si nous voulons calculer le $(d+1)$-ième chiffre hexadécimal de $\pi$, 

- Nous multiplions $\pi$ par $16^d$.
- Nous ne gardons que la partie fractionnaire du résultat.
- Nous prenons le premier chiffre hexadécimal de ce que nous venons de trouver.

## 2. L'algorithme de Bailey, Borwein et Plouffe (BBP)

### 2.1 Partie fractionnaire

Notons, pour tout réel $x\ge 0$, $x\bmod 1=x-\lfloor x\rfloor$ la partie fractionnaire de $x$.

In [ ]:
def frac(x):
    return x - math.floor(x)

Pour $q=1,4,5,6$, posons 

$$S_q = \sum_{i=0}^\infty \frac 1 {16^i}\frac{1}{8i+q}$$

Soit $d\ge 0$. On a

$$(16^d S_q)\bmod 1=\sum_{i=0}^d \frac{16^{d-i}}{8i+q} \bmod 1+\sum_{i=d+1}^\infty \frac{16^{d-i}}{8i+q}\bmod 1$$

ou encore

$$(16^d S_q)\bmod 1=\sum_{i=0}^d \frac{16^{d-i}\bmod (8i + q)}{8i+q} \bmod 1+\sum_{i=d+1}^\infty \frac{16^{d-i}}{8i+q}\bmod 1$$

Notons dans ce qui suit

$$S_{dq}=\sum_{i=0}^d \frac{16^{d-i}\bmod (8i + q)}{8i+q} \bmod 1$$

et

$$S'_{dq}=\sum_{i=d+1}^\infty \frac{16^{d-i}}{8i+q}\bmod 1$$

### 2.2 Le calcul de $S_{dq}$

Ce calcul demande l'évaluation de $16^{d-i}$ modulo $8i+q$. Pour cela, on utilise une exponentiation rapide. La fonction `puissance` prend en paramètres trois entiers $x,n,p$. Elle renvoie $x^n\bmod p$.

In [ ]:
def puissance(x, n, p):
    z = 1
    m = n
    y = x
    while m != 0:
        if m % 2 == 1:
            z = (z * y) % p
        m = m // 2
        y = (y * y) % p
    return z

In [ ]:
puissance(2, 10000000000, 10000)

La somme $S_{dq}$ est alors facilement calculable.

In [ ]:
def somme1(d, q):
    s = 0
    for i in range(d + 1):
        s = frac(s + puissance(16, d - i, 8 * i + q) / (8 * i + q))
    return s

In [ ]:
somme1(10 ** 5, 1)

### 2.3 Le calcul de $S'_{dq}$

Pour le calcul de $S'_{dq}$ on se contente d'additionner un certain nombre de ses termes, $N$ disons, en virgule flottante. Bref, on approche $S'_{dq}$ par 

$$\sum_{i=d+1}^{d+N} \frac{16^{d-i}}{8i+q}$$

Combien prendre pour $N$ ? Eh bien l'erreur commise est

$$\sum_{i=d+N+1}^\infty \frac{16^{d-i}}{8i+q}\le \sum_{i=d+N+1}^\infty 16^{d-i}=\frac 1 {16^{N+1}}\sum_{k=0}^\infty\frac 1 {16^k}=\frac{1}{15\times 16^{N}}$$

Si l'on veut une erreur inférieure à $10^{-16}$, valeur raisonnable pour des calculs sur des flottants, il suffit donc de choisir $N$ tel que $15\times 16^{N}\ge 10^{16}$. Passons au logarithme décimal :

$$N\log 16+\log 15\ge 16$$

c'est à dire

$$N\ge \frac{16-\log 15}{\log 16}$$

In [ ]:
(16 - math.log(15, 10)) / math.log(16, 10)

Soyons généreux et prenons 15 termes pour le calcul de la somme en question.

In [ ]:
def somme2(d, q):
    s = 0
    for i in range(d + 1, d + 16):
        s = frac(s + 16 ** (d - i) / (8 * i + q))
    return s

In [ ]:
somme2(10 ** 5, 1)

### 2.4 BBP, enfin

Tout a été fait, il n'y a plus qu'à additionner. La fonction `somme`, tout d'abord, renvoie $S_{dq}+S'_{dq}$.

In [ ]:
def somme(d, q):
    return somme1(d, q) + somme2(d, q)

In [ ]:
somme(10 ** 5, 1)

La fonction BBP renvoie une valeur approchée de $(16^d\pi)\bmod 1$.

In [ ]:
def BBP(d):
    s = frac(4 * somme(d, 1) - 2 *  somme(d, 4) - somme(d, 5) - somme(d, 6))
    return s

In [ ]:
BBP(10 ** 5 - 1)

## 3. Fiabilité des résultats

### 3.1 Comptons les opérations

La valeur renvoyée par BBP est-elle correcte ? Après tout nous faisons des calculs en virgule flottante ! Python utilise pour ces calculs le format IEE754, qui garantit une erreur d'au plus 1 bit sur le dernier chiffre pour chaque opération. Combien avons nous effectué d'opérations en virgule flottante ?

Nous effectuons 4 sommes de $d$ termes. Pour chaque terme on fait une division. Cela nous donne donc $8d-4$ opérations : $4d$ divisions et $4(d-1)$ additions.

Nous effectuons également 4 sommes de 15 termes : pour chaque terme il y a un calacul de puissance en flottants et une division. Au total $8\times 15 + 56=176$ opérations en virgule flottante.

Au total, nous faisons donc $8d+176$ opérations en virgule flottante. Rajoutons quelques additions (il y a 8 sommes à ajouter), une multiplication par 4 et une multiplication par 2. Nous arrivons $8d+185$ opérations (en ai-je oublié ?).

Imaginons qu'à chaque opération l'erreur de 1 bit s'ajoute aux précédentes. Ceci est très pessimiste ! Nous aurons à la fin de nos calcul un nombre de bits erronés de l'ordre de $\log_2(8d+185)$.

In [ ]:
def bits_erreur(d):
    return math.log(8 * d + 185, 2)

In [ ]:
bits_erreur(10 ** 6)

Python calcule sur 52 bits. Combien de bits exacts de façon sûre ?

In [ ]:
def bits_exacts(d):
    return 52 - bits_erreur(d)

In [ ]:
bits_exacts(10 ** 6)

Sachant qu'un chiffre en hexadécimal est constitué de 4 bits, combien de chiffres hexadécimaux exacts ?

In [ ]:
def hexa_exacts(d):
    return math.floor(bits_exacts(d)) // 4

In [ ]:
hexa_exacts(10 ** 6)

En lançant `BBP(10 ** 6 - 1)` nous aurons donc de façon sûre les chiffres 1000000 à 1000006 du nombre $\pi$.

### 3.2 Convertissons en hexadécimal

La fonction `vers_hexa` prend un réel $x\in[0,1[$ en paramètre et renvoie une chaîne de caractères qui contient les dix premiers chiffres du développement hexadécimal de $x$. Lisez la fonction, elle ne pose aucune difficulté.

In [ ]:
def vers_hexa(x):
    s = ''
    for k in range(10):
        y = 16 * x
        c = math.floor(y)
        s = s + chiffre_hexa(c)
        x = frac(y)
    return s

La fonction `vers_hexa` utilise `chiffre_hexa` qui prend en paramètre un entier $c$ entre 0 et 15 et renvoie le "chiffre" hexadécimal correspondant.

In [ ]:
def chiffre_hexa(c):
    if c <= 9: return str(c)
    elif c == 10: return 'A'
    elif c == 11: return 'B'
    elif c == 12: return 'C'
    elif c == 13: return 'D'
    elif c == 14: return 'E'
    elif c == 15: return 'F'

### 3.3 Nous y sommes

#### 3.3.1 Cent mille

Quelle est le cent-millième chiffre hexadécimal de $\pi$ ?

In [ ]:
vers_hexa(BBP(10 ** 5 - 1))

C'est un 5. Et les chiffres suivants ? Sont-ils corrects ?

In [ ]:
hexa_exacts(10 ** 5)

On peut donc garantir les 8 chiffres `535EA16C`.

#### 3.3.1 Un million

Quelle est le millionième chiffre hexadécimal de $\pi$ ? Soyez patients, environ une minute de calcul sur ma machine. Python n'est pas fort en boucles `for`, et on ne fait que des boucles `for` :-).

In [ ]:
vers_hexa(BBP(10 ** 6 - 1))

C'est un 2. Et les chiffres suivants ? Combien sont corrects ?

In [ ]:
hexa_exacts(10 ** 6)

On peut donc garantir les 7 chiffres `26C65E5`. Au cas où vous vous poseriez la question, il s'avère que les chiffres `2CB` sont également corrects (voir l'article BBP). Mais on ne peut pas les __garantir__ avec cet algorithme.

#### 3.3.1 Dix millions

Quelle est le dix-millionième chiffre hexadécimal de $\pi$ ? Soyez infiniment patients. Allez prendre un petit café, cela va prendre 10 fois plus de temps que pour un million (donc, dix minutes environ).

In [ ]:
vers_hexa(BBP(10 ** 7 - 1))

C'est un 1. Et les chiffres suivants ? Sont-ils corrects ?

In [ ]:
hexa_exacts(10 ** 7)

On peut donc garantir les 6 chiffres `17AF58`. Il s'avère que les chiffres `63` sont également corrects (voir l'article BBP). Les deux suivants sont `EF` alors que notre fonction renvoie les chiffres erronés `F0`.

## 4. Et en base 10 ?

Bien évidemment, tout le monde meurt d'envie de savoir si une telle formule existe pour la base 10. Borwein, Borwein et Galway ont montré que ce genre de formule ne peut pas exister. Je resterai vague là-dessus, et me contenterai de citer leur article :

" _Of particular interest, we show that $\pi$ has no Machin-type BBP arctangent formula when $b\ne 2$. To the best of our knowledge, when there is no Machin-type BBP formula for a constant then no BBP formula of any form is known for that constant_ ".

La référence de l'article est :

J. Borwein, D. Borwein, W. Galway, _Finding and Excluding $b$-ary Machin-Type Individual Digit Formulae_, Canadian Journal of Mathematics, Vol. 56 (5), 2004, Pages 897-925.

Il convient pour terminer de remarquer que des algorithmes permettant le calcul des décimales individuelles de $\pi$ existent mais, à l'heure actuelle, ces algorithmes sont moins efficaces que ceux qui consistent à calculer toutes les décimales. 